# DSCI100 group 12 project: **Pulsar star classification**

**(1).Introduction**

To understand what pulsar stars are we must first understand what neutron stars are. Neutron stars are formed when a massive star runs out of fuel and collapses onto itself, thus forming one of the universe's densest bodies(1). Of these neutron stars, most of them are categorized as pulsar stars. Pulsar stars are rotating neutron stars that have pulses of radiation at very regular intervals with a very strong magnetic field(1). From earth, we can observe the light pulsar stars emit that sweep across like a lighthouse. Each pulsar star emits a slightly different emission pattern that we can use to identify them(2). Machine learning has been used to identify and label these pulsar candidates for analysis(2). 

These pulsar stars are of considerable scientific interest as probes of space-time, interstellar mediums, and states of matter. Since not all neutron stars are pulsar stars we want to be able to identify and classify the ones we think are candidates. To do this we will need to create a classification model that takes features of the pulsar star to predict the “class” of a subject. 

We used a dataset called HTRU2 that describes a sample of candidate data collected during the High Time Resolution Universe survey and the raw data was collected through the Parkes Observatory(2). This dataset can be treated as a binary classification problem where the real pulsar examples are the minority positive class and the spurious examples the majority negative class. It contains RFI/noise 16,259 spurious examples, and 1,639 real pulsar examples where these examples have been checked through by human annotators(2). Each row lists the variables first, with the class labels, 0(negative) and 1(positive), as the final entry. The variables with “profile” mean the integrated pulse profile of the candidate and the DMR variables are components of the dispersion measure signal-to-noise ratio data.
.


**(2).Methods & Results**

First, we import the Python package directly from the HTRU2 dataset url page and do some preparatory work.

In [5]:
import random

import altair as alt
import pandas as pd
import numpy as np
from sklearn.preprocessing import StandardScaler
from sklearn.compose import make_column_transformer
from sklearn.compose import make_column_selector
from sklearn.neighbors import KNeighborsClassifier
from sklearn.pipeline import make_pipeline
from sklearn.model_selection import train_test_split
from sklearn.metrics.pairwise import euclidean_distances
from sklearn import set_config
from sklearn.metrics.pairwise import euclidean_distances
from sklearn.model_selection import (
    GridSearchCV,
    RandomizedSearchCV,
    cross_validate,
    train_test_split,
)

# Simplify working with large datasets in Altair
alt.data_transformers.disable_max_rows()

# Output dataframes instead of arrays
set_config(transform_output="pandas")

Then, we load data from the web.

In [6]:
pip install ucimlrepo

Note: you may need to restart the kernel to use updated packages.


In [7]:
from ucimlrepo import fetch_ucirepo 
# fetch dataset 
htru2 = fetch_ucirepo(id=372) 
  
# data (as pandas dataframes) 
X = htru2.data.features 
y = htru2.data.targets 
  
# metadata 
print(htru2.metadata) 
  
# variable information 
print(htru2.variables) 

{'uci_id': 372, 'name': 'HTRU2', 'repository_url': 'https://archive.ics.uci.edu/dataset/372/htru2', 'data_url': 'https://archive.ics.uci.edu/static/public/372/data.csv', 'abstract': 'Pulsar candidates collected during the HTRU survey. Pulsars are a type of star, of considerable scientific interest. Candidates must be classified in to pulsar and non-pulsar classes to aid discovery.', 'area': 'Physics and Chemistry', 'tasks': ['Classification', 'Clustering'], 'characteristics': ['Multivariate'], 'num_instances': 17898, 'num_features': 8, 'feature_types': ['Real'], 'demographics': [], 'target_col': ['class'], 'index_col': None, 'has_missing_values': 'no', 'missing_values_symbol': None, 'year_of_dataset_creation': 2015, 'last_updated': 'Wed Apr 03 2024', 'dataset_doi': '10.24432/C5DK6R', 'creators': ['Robert Lyon'], 'intro_paper': {'title': 'Fifty years of pulsar candidate selection: from simple filters to a new principled real-time classification approach', 'authors': 'R. Lyon, B. Stapper

From this, we got two split dataframes. We end up with X, which is the dataframe with predictors, and y, which is the dataframe with classes. Now, we merge them together into one dataframe and reset the index.

In [8]:
star_data_origin = pd.merge(X, y, left_index=True,right_index=True).reset_index().drop(columns="index")
star_data_origin

Profile_mean  Profile_stdev  Profile_skewness  Profile_kurtosis  \
0        140.562500      55.683782         -0.234571         -0.699648   
1        102.507812      58.882430          0.465318         -0.515088   
2        103.015625      39.341649          0.323328          1.051164   
3        136.750000      57.178449         -0.068415         -0.636238   
4         88.726562      40.672225          0.600866          1.123492   
...             ...            ...               ...               ...   
17893    136.429688      59.847421         -0.187846         -0.738123   
17894    122.554688      49.485605          0.127978          0.323061   
17895    119.335938      59.935939          0.159363         -0.743025   
17896    114.507812      53.902400          0.201161         -0.024789   
17897     57.062500      85.797340          1.406391          0.089520   

          DM_mean   DM_stdev  DM_skewness  DM_kurtosis  class  
0        3.199833  19.110426     7.975532    74.242225      0  
1        1.677258  14.860146    10.576487   127.393580      0  
2        3.121237  21.744669     7.735822    63.171909      0  
3        3.642977  20.959280     6.896499    53.593661      0  
4        1.178930  11.468720    14.269573   252.567306      0  
...           ...        ...          ...          ...    ...  
17893    1.296823  12.166062    15.450260   285.931022      0  
17894   16.409699  44.626893     2.945244     8.297092      0  
17895   21.430602  58.872000     2.499517     4.595173      0  
17896    1.946488  13.381731    10.007967   134.238910      0  
17897  188.306020  64.712562    -1.597527     1.429475      0  

[17898 rows x 9 columns]

*Table 1: Original star data*

Now, we get Table 1 which can be used for future analysis. 
We can see that there are 8 predictors, which is alot and it would be unnecessary to use all of them so, it would be better if we only selected a few of them to predict the class.
Thus, to decide which predictors to use for our model, we used a pairplot to compare the relationships between different predictors. Then we selected a set of them where two predictors showed a strong positive relationship. First, we created a preprocessor to standardize the data, which makes all data observations of a comparable scale.

In [9]:
preprocessor = make_column_transformer(
    (StandardScaler(), ["Profile_mean", "Profile_stdev", "Profile_skewness"
                        ,"Profile_kurtosis", "DM_mean", "DM_stdev", "DM_skewness"
                        ,"DM_kurtosis"]),
    remainder = "passthrough",
    verbose_feature_names_out = False 
)
preprocessor = preprocessor.fit(star_data_origin) #fit in the dataframe
scaled_star = preprocessor.transform(star_data_origin) #perform the change
scaled_star

Profile_mean  Profile_stdev  Profile_skewness  Profile_kurtosis  \
0          1.149317       1.334832         -0.669570         -0.400459   
1         -0.334168       1.802265         -0.011785         -0.370535   
2         -0.314372      -1.053322         -0.145233         -0.116593   
3          1.000694       1.553254         -0.513409         -0.390178   
4         -0.871402      -0.858879          0.115609         -0.104866   
...             ...            ...               ...               ...   
17893      0.988208       1.943284         -0.625655         -0.406697   
17894      0.447319       0.429062         -0.328831         -0.234643   
17895      0.321842       1.956220         -0.299334         -0.407492   
17896      0.133628       1.074510         -0.260050         -0.291041   
17897     -2.105762       5.735470          0.872674         -0.272508   

        DM_mean  DM_stdev  DM_skewness  DM_kurtosis  class  
0     -0.319440 -0.370625    -0.072798    -0.287438      0  
1     -0.371102 -0.588924     0.504427     0.211581      0  
2     -0.322107 -0.235328    -0.125996    -0.391373      0  
3     -0.304404 -0.275666    -0.312265    -0.481300      0  
4     -0.388010 -0.763111     1.324026     1.386794      0  
...         ...       ...          ...          ...    ...  
17893 -0.384010 -0.727295     1.586054     1.700034      0  
17894  0.128776  0.939926    -1.189159    -0.906574      0  
17895  0.299137  1.671568    -1.288079    -0.941330      0  
17896 -0.361967 -0.664857     0.378257     0.275850      0  
17897  5.961291  1.971546    -2.197327    -0.971052      0  

[17898 rows x 9 columns]

*Table 2: Standardized original star data*

Then, we created a pairplot which contains the scatter plot of each pair of columns that we are plotting, so that we can explore the pairwise relationship between the variables.

In [10]:
columns_to_plot = ["Profile_mean", "Profile_stdev", "Profile_skewness"
                        ,"Profile_kurtosis", "DM_mean", "DM_stdev", "DM_skewness"
                        ,"DM_kurtosis"]

star_pairplot = alt.Chart(scaled_star).mark_point().encode(
    alt.X(alt.repeat("row"), type="quantitative"),
    alt.Y(alt.repeat("column"), type="quantitative"),
).properties(
    width=150,
    height=150
).repeat(
    column=columns_to_plot,
    row=columns_to_plot
)
star_pairplot

alt.RepeatChart(...)

*Figure 1: Pairplot of predictors*

From Figure 1, we notice that "DM_kurtosis" and "DM_skewness" have strong linear positive relationships. "Profile_kurtosis" and "Profile_skewness" also have strong linear positive relationships.
Thus, we could choose one set of these predictors to use for predictions, since they will both influence the results similarly.
In this case, we chose "DM_kurtosis" and "Profile_skewness". Now, we can select the columns that we will use to predict the class and drop the unused columns, "Profile_kurtosis" and "DM_skewness".

In [11]:
star_data = star_data_origin[["Profile_mean", "Profile_stdev", "Profile_skewness", "DM_mean", "DM_stdev", "DM_kurtosis","class"]]
star_data

Profile_mean  Profile_stdev  Profile_skewness     DM_mean   DM_stdev  \
0        140.562500      55.683782         -0.234571    3.199833  19.110426   
1        102.507812      58.882430          0.465318    1.677258  14.860146   
2        103.015625      39.341649          0.323328    3.121237  21.744669   
3        136.750000      57.178449         -0.068415    3.642977  20.959280   
4         88.726562      40.672225          0.600866    1.178930  11.468720   
...             ...            ...               ...         ...        ...   
17893    136.429688      59.847421         -0.187846    1.296823  12.166062   
17894    122.554688      49.485605          0.127978   16.409699  44.626893   
17895    119.335938      59.935939          0.159363   21.430602  58.872000   
17896    114.507812      53.902400          0.201161    1.946488  13.381731   
17897     57.062500      85.797340          1.406391  188.306020  64.712562   

       DM_kurtosis  class  
0        74.242225      0  
1       127.393580      0  
2        63.171909      0  
3        53.593661      0  
4       252.567306      0  
...            ...    ...  
17893   285.931022      0  
17894     8.297092      0  
17895     4.595173      0  
17896   134.238910      0  
17897     1.429475      0  

[17898 rows x 7 columns]

*Table 3: Star data with selected predictors*

Then, we use head function to select the first 5 rows of Table 3.

In [12]:
star_data_head = star_data.head()
star_data_head

Profile_mean  Profile_stdev  Profile_skewness   DM_mean   DM_stdev  \
0    140.562500      55.683782         -0.234571  3.199833  19.110426   
1    102.507812      58.882430          0.465318  1.677258  14.860146   
2    103.015625      39.341649          0.323328  3.121237  21.744669   
3    136.750000      57.178449         -0.068415  3.642977  20.959280   
4     88.726562      40.672225          0.600866  1.178930  11.468720   

   DM_kurtosis  class  
0    74.242225      0  
1   127.393580      0  
2    63.171909      0  
3    53.593661      0  
4   252.567306      0

*Table 4: first 5 rows of Table 3*

Here, "Profile_mean" means the calculated mean of the integrated pulse profile, "Profile_stdev" means the calculated standard deviation 
of the integrated pulse profile, "Profile_skewness" means the skewness of the 
integrated pulse  profie,
 "DM_mean"means  the calculated mean of the DM-SNR curve, "DM_stdev" means the calculated standard deviation of the  DM-SNR curve,  "DM_kurtosis"  means  the excess kurtosis of
the DM-SNR curve, and lastly "class" represents the class labels given to the candidate(positive and negative). Now, we can start our process of predicting the class using these six predictors. First, we split the dataframe into two parts. One is the training data and the other is the testing data. Here, we use a random seed which is necessary to make sure the autotesting code functions properly.

In [25]:
np.random.seed(2024)

star_train, star_test = train_test_split(
    star_data, train_size=0.80,
)
star_train

Profile_mean  Profile_stdev  Profile_skewness     DM_mean   DM_stdev  \
14117     89.726562      42.207026          0.414897    2.403846  13.488690   
3787     116.960938      73.153990          0.316964  201.534281  47.262251   
765      136.664062      52.628307          0.067857    4.382107  24.805369   
9684     116.046875      43.673837          0.330900    3.107023  20.456870   
8149     118.843750      48.989865          0.335433    0.775084  11.946176   
...             ...            ...               ...         ...        ...   
16567    128.125000      48.357555         -0.005863    2.019231  15.440807   
2494     135.554688      41.715706         -0.047587    2.617893  17.409786   
14875    124.976562      45.683946         -0.209657    4.981605  26.593647   
2688     125.304688      49.947873          0.053109    1.628763  12.247147   
7816     120.867188      39.129267          0.068661    2.090301  13.255599   

       DM_kurtosis  class  
14117   121.734406      0  
3787      2.788871      0  
765      49.054326      0  
9684     69.309930      0  
8149    312.061142      0  
...            ...    ...  
16567   137.918490      0  
2494     89.780556      0  
14875    31.319089      0  
2688    195.921439      0  
7816    152.782160      0  

[14318 rows x 7 columns]

*Table 5: Training data*

Then, we want to find the best K value. To do this we will need to try different values of neighbours, and use cross-validation to calculate an accuracy for each value of K in a reasonable range. Next, we figure out the value of K that gives the highest accuracy on the validation data. Finally, we can then build a model using that selected K value.
To begin, we built a preprocessor first to standardize the data to ensure all data observations will be on a comparable scale and contribute equal shares to the calculation of the distance between points.
Otherwise, one variable may skew the classification results.

In [14]:
star_preprocessor = make_column_transformer(
    (StandardScaler(), ["Profile_mean", "Profile_stdev", "Profile_skewness", "DM_mean", "DM_stdev", "DM_kurtosis"]),
     verbose_feature_names_out=False
)
star_preprocessor

ColumnTransformer(transformers=[('standardscaler', StandardScaler(),
                                 ['Profile_mean', 'Profile_stdev',
                                  'Profile_skewness', 'DM_mean', 'DM_stdev',
                                  'DM_kurtosis'])],
                  verbose_feature_names_out=False)

Then, we defined the grid of values that we wanted to explore, and defined the pipeline without specifying a particular value of K.

In [15]:
param_grid = {
    "kneighborsclassifier__n_neighbors": range(2, 15, 1),
}
star_pipe = make_pipeline(star_preprocessor, KNeighborsClassifier())

Next, we are ready to create the GridSearchCV object.

In [16]:
knn_star_grid = GridSearchCV(
    estimator=star_pipe, 
    param_grid=param_grid, 
    cv=5,
    n_jobs=-1,
)
knn_star_grid

GridSearchCV(cv=5,
             estimator=Pipeline(steps=[('columntransformer',
                                        ColumnTransformer(transformers=[('standardscaler',
                                                                         StandardScaler(),
                                                                         ['Profile_mean',
                                                                          'Profile_stdev',
                                                                          'Profile_skewness',
                                                                          'DM_mean',
                                                                          'DM_stdev',
                                                                          'DM_kurtosis'])],
                                                          verbose_feature_names_out=False)),
                                       ('kneighborsclassifier',
                                        KNeighborsClassifier())]),
             n_jobs=-1,
             param_grid={'kneighborsclassifier__n_neighbors': range(2, 15)})

Now we use the fit method on the GridSearchCV object and pass the training data, with predictors and classes as the two arguments, to fit. 
We will also create a new dataframe that contains the resulting cross-validation accuracy estimate for each choice of n_neighbors.

In [17]:
X = star_train.drop(columns=["class"])
y = star_train["class"]

knn_model_grid = knn_star_grid.fit(X, y)

accuracies_grid = pd.DataFrame(knn_model_grid.cv_results_)
accuracies_grid

mean_fit_time  std_fit_time  mean_score_time  std_score_time  \
0        0.021951      0.009051         0.131249        0.005250   
1        0.011692      0.000594         0.128345        0.001598   
2        0.011213      0.000087         0.126937        0.000575   
3        0.011154      0.000103         0.127802        0.000353   
4        0.011459      0.000284         0.131808        0.001672   
5        0.011258      0.000119         0.131559        0.001264   
6        0.011209      0.000220         0.132733        0.000911   
7        0.011214      0.000099         0.135986        0.001922   
8        0.011286      0.000166         0.135865        0.004782   
9        0.011164      0.000100         0.135637        0.001669   
10       0.011350      0.000182         0.137233        0.001675   
11       0.011199      0.000094         0.138044        0.001341   
12       0.011176      0.000068         0.138084        0.000579   

   param_kneighborsclassifier__n_neighbors  \
0                                        2   
1                                        3   
2                                        4   
3                                        5   
4                                        6   
5                                        7   
6                                        8   
7                                        9   
8                                       10   
9                                       11   
10                                      12   
11                                      13   
12                                      14   

                                       params  split0_test_score  \
0    {'kneighborsclassifier__n_neighbors': 2}           0.974860   
1    {'kneighborsclassifier__n_neighbors': 3}           0.978701   
2    {'kneighborsclassifier__n_neighbors': 4}           0.977304   
3    {'kneighborsclassifier__n_neighbors': 5}           0.978352   
4    {'kneighborsclassifier__n_neighbors': 6}           0.977654   
5    {'kneighborsclassifier__n_neighbors': 7}           0.979050   
6    {'kneighborsclassifier__n_neighbors': 8}           0.978003   
7    {'kneighborsclassifier__n_neighbors': 9}           0.977654   
8   {'kneighborsclassifier__n_neighbors': 10}           0.978352   
9   {'kneighborsclassifier__n_neighbors': 11}           0.979050   
10  {'kneighborsclassifier__n_neighbors': 12}           0.978352   
11  {'kneighborsclassifier__n_neighbors': 13}           0.979050   
12  {'kneighborsclassifier__n_neighbors': 14}           0.979050   

    split1_test_score  split2_test_score  split3_test_score  \
0            0.974511           0.978352           0.976249   
1            0.975908           0.980098           0.978344   
2            0.977304           0.977654           0.977646   
3            0.975908           0.979399           0.978694   
4            0.976955           0.979399           0.977995   
5            0.977304           0.979399           0.977995   
6            0.976257           0.979050           0.979392   
7            0.978352           0.979050           0.978694   
8            0.976606           0.979050           0.977995   
9            0.978003           0.979399           0.977646   
10           0.976955           0.980098           0.977297   
11           0.976955           0.979749           0.977995   
12           0.976257           0.978701           0.978694   

    split4_test_score  mean_test_score  std_test_score  rank_test_score  
0            0.972057         0.975206        0.002074               13  
1            0.973804         0.977371        0.002237               11  
2            0.975899         0.977162        0.000650               12  
3            0.975550         0.977581        0.001553                9  
4            0.976249         0.977650        0.001061                7  
5            0.976249         0.978000        0.001150                2  
6            0.976598         0.977860        0.0012

*Table 6: Cross-validation accuracy estimate*

From here, we can decide which number of k-neighbors is best by plotting the accuracy versus K, based on Table 6.

In [18]:
accuracy_versus_k_grid = alt.Chart(accuracies_grid, title = "accuracy of different K value" ).mark_line(point=True).encode(
     x=alt.X("param_kneighborsclassifier__n_neighbors")
         .title("Neighbors")
         .scale(zero=False),
     y=alt.Y("mean_test_score")
         .title("Accuracy estimate")
         .scale(zero=False)
 ).properties(
    width=600
)

accuracy_versus_k_grid

alt.Chart(...)

*Figure 2: Accuracy versus K plot*

From Figure 2, we can find that K = 11 provides the highest accuracy, so now we can use K = 11 to estimate the class. We can then create a new pipeline with K=11 and fit it with the training data.

In [19]:
knn_spec = KNeighborsClassifier(n_neighbors=11)
star_pipe_final = make_pipeline(star_preprocessor,knn_spec)

X = star_train.drop(columns=["class"])
y = star_train["class"]

star_final_fit = star_pipe_final.fit(X,y)
star_final_fit

Pipeline(steps=[('columntransformer',
                 ColumnTransformer(transformers=[('standardscaler',
                                                  StandardScaler(),
                                                  ['Profile_mean',
                                                   'Profile_stdev',
                                                   'Profile_skewness',
                                                   'DM_mean', 'DM_stdev',
                                                   'DM_kurtosis'])],
                                   verbose_feature_names_out=False)),
                ('kneighborsclassifier', KNeighborsClassifier(n_neighbors=11))])

Here we have the K-nearest neighbors classifier object we can use to predict the class labels for our test set.
To do this, we created a new column in the testing dataframe called "predicted" that contains the predicted diagnoses from the classifier.

In [20]:
star_test_predictions = star_test.assign(
    predicted=star_final_fit.predict(star_test[["Profile_mean", "Profile_stdev", "Profile_skewness", "DM_mean", "DM_stdev", "DM_kurtosis"]])
)
star_test_predictions

Profile_mean  Profile_stdev  Profile_skewness    DM_mean   DM_stdev  \
12886     88.148438      39.451729          0.605601   2.527592  15.288149   
8692     109.453125      48.281055          0.126580   2.988294  20.520604   
17650    144.242188      49.522840         -0.108100  11.497492  45.517766   
1781     124.500000      53.521608          0.034350   2.151338  17.634329   
13889    100.312500      48.392398          0.714821   2.263378  18.163970   
...             ...            ...               ...        ...        ...   
10090    136.125000      57.965237          0.157111   2.382107  16.117731   
8559     116.546875      49.238079          0.388811   0.999164  11.771195   
5129     131.671875      51.689444         -0.083764   7.989967  34.976269   
15693    107.539062      60.053479          0.049761   1.454849  11.566102   
6006     109.164062      46.074291          0.258365   1.003344  11.414580   

       DM_kurtosis  class  predicted  
12886   110.292943      0          0  
8692     64.666993      0          0  
17650    15.098706      0          0  
1781    101.933256      0          0  
13889   107.651216      0          0  
...            ...    ...        ...  
10090   100.398098      0          0  
8559    299.638780      0          0  
5129     20.265613      0          0  
15693   220.034326      0          0  
6006    293.475994      0          0  

[3580 rows x 8 columns]

*Table 7: Testing data with predictions*

Finally, we will assess our classifier’s performance. First, we will examine the accuracy. To do this we will pass the same test data for the predictors that we originally passed when making predictions, and then use the score function to calculate the accuracy.

In [21]:
X_test = star_test[["Profile_mean", "Profile_stdev", "Profile_skewness", "DM_mean", "DM_stdev", "DM_kurtosis"]]
y_test = star_test["class"]

star_prediction_accuracy = star_final_fit.score(X_test, y_test)
star_prediction_accuracy

0.9812849162011174

This shows us that the accuracy of our model is around 98%. Finally, we can look at the confusion matrix for the classifier.

In [22]:
star_mat = pd.crosstab(
    star_test_predictions["class"],  # True labels
    star_test_predictions["predicted"],  # Predicted labels
)
star_mat

predicted     0    1
class               
0          3230   22
1            45  283

*Table 8: Confusion matrix*

Then, we assign one label as positive and another as negative.
Here we are more interested in 1 (which means it is pulsar star) so we assign it as positive.
Table 8 shows 283 observations were correctly predicted as 1, and 3230 were correctly predicted as 0. It also shows that the classifier made some mistakes; in particular, it classified 45 observations as 0 when they were actually 1, and 22 observations as 1 when they were actually 0.
Now, we can calculate the precision and recall based on the formulas below: 

precision = 
number of correct positive predictions / total number of positive predictions

recall =
number of correct positive predictions / total number of positive test set observations

In [23]:
precision = 218 / ( 218 + 14)
precision

0.9396551724137931

In [24]:
recall = 218 / (218 + 49)
recall

0.8164794007490637

From this we can tell that the precision is about 93% and the recall is about 82%.

**(3).Discussion**

Michael can edit it.

**(4)References**

(1) Neutron Stars, Pulsars, and Magnetars - Introduction. Imaginegsfcnasagov. https://imagine.gsfc.nasa.gov/science/objects/neutron_stars1.html#:~:text=Pulsars%20are%20rotating%20neutron%20stars.

(2) R. J. Lyon, B. W. Stappers, S. Cooper, J. M. Brooke, J. D. Knowles, Fifty Years of Pulsar Candidate Selection: From simple filters to a new principled real-time classification approach, Monthly Notices of the Royal Astronomical Society 459 (1), 1104-1123, DOI: 10.1093/mnras/stw656

(3) R. J. Lyon, HTRU2, DOI: 10.6084/m9.figshare.3080389.v1.
